In [1]:
import tensorflow as tf
import keras
import numpy as np

from keras.models import Model
from keras.layers import Dense
from keras.utils import plot_model

from keras.preprocessing import image

# NasNet
from keras.applications.nasnet import NASNetMobile
from keras.applications.nasnet import preprocess_input

# ResNext
#from keras_applications.resnext import ResNeXt101
#from keras_applications.resnext import preprocess_input

Using TensorFlow backend.


In [2]:
ckPtDir = "log/segnet"
plotDir = "log/plot"

In [3]:
base_model = NASNetMobile(include_top=False, backend = keras.backend, layers = keras.layers, models = keras.models, utils = keras.utils)
#base_model = ResNeXt101(include_top=False, backend = keras.backend, layers = keras.layers, models = keras.models, utils = keras.utils)

x = base_model.output
predictions = Dense(2048, activation='softmax')(x)

model = Model(inputs=base_model.input, outputs=predictions)
model.summary()

Instructions for updating:
If using Keras pass *_constraint arguments to layers.


Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 224, 224, 3)  0                                            
__________________________________________________________________________________________________
stem_conv1 (Conv2D)             (None, 111, 111, 32) 864         input_1[0][0]                    
__________________________________________________________________________________________________
stem_bn1 (BatchNormalization)   (None, 111, 111, 32) 128         stem_conv1[0][0]                 
__________________________________________________________________________________________________
activation_1 (Activation)       (None, 111, 111, 32) 0           stem_bn1[0][0]                   
_________

In [4]:
plot_model(model, show_shapes=True, to_file= plotDir + '/nasNet.png')

In [5]:
img_path = 'test.png'
img = image.load_img(img_path, target_size=(224, 224))
x = image.img_to_array(img)
x = np.expand_dims(x, axis=0)
x = preprocess_input(x)

preds = model.predict(x)
print(preds)


[[[[5.3962733e-04 4.9938634e-04 4.9084582e-04 ... 5.0317758e-04
    4.6600748e-04 4.8994599e-04]
   [4.8828125e-04 4.8828125e-04 4.8828125e-04 ... 4.8828125e-04
    4.8828125e-04 4.8828125e-04]
   [2.9332342e-04 5.0441630e-04 4.6141457e-04 ... 3.7040890e-04
    6.2806543e-04 4.3672384e-04]
   ...
   [1.9583835e-04 8.8391232e-04 2.0944253e-04 ... 7.0811511e-05
    6.6173711e-04 9.6016200e-05]
   [4.9658044e-04 4.4471415e-04 4.3690469e-04 ... 4.4689502e-04
    5.0146901e-04 5.0787273e-04]
   [4.3550256e-04 4.8065360e-04 4.8349411e-04 ... 4.8187986e-04
    5.0286629e-04 4.9429777e-04]]

  [[4.8828125e-04 4.8828125e-04 4.8828125e-04 ... 4.8828125e-04
    4.8828125e-04 4.8828125e-04]
   [4.5631724e-04 5.1339914e-04 5.0010497e-04 ... 4.8021015e-04
    4.9308868e-04 4.7968756e-04]
   [2.0726975e-04 7.9282350e-04 8.9528091e-04 ... 2.5318950e-04
    4.6223751e-04 1.3212171e-04]
   ...
   [2.8399631e-04 5.4654351e-04 6.6614355e-04 ... 4.9128084e-05
    6.1388238e-04 6.5439948e-05]
   [6.0274021

In [6]:
from keras.preprocessing import sequence
from keras.models import Sequential
from keras.layers import Dense, Embedding, Activation, LSTM, CuDNNGRU, CuDNNLSTM
from keras.layers import Dropout, Conv1D, MaxPooling1D, GlobalMaxPool1D
from keras.layers import Bidirectional, InputLayer

from keras import regularizers
from keras.callbacks import EarlyStopping, ModelCheckpoint

In [7]:
EMB_SIZE = 128
BATCH_SIZE = 512
MAX_LEN = 200
max_features = 20000

In [8]:
def Model():
    model = Sequential()
    model.add(Embedding(max_features, EMB_SIZE, input_length=MAX_LEN))    
    model.add(Bidirectional(CuDNNLSTM(64, return_sequences=True)))
    model.add(GlobalMaxPool1D())
    model.add(Dropout(0.2))
    model.add(Dense(64, activation='relu'))
    model.add(Dense(1, activation='sigmoid'))
    
    return model

In [9]:
model = Model()
model.compile(loss=tf.keras.losses.BinaryCrossentropy(), optimizer='adam', metrics=['accuracy'])
model.summary()

Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_1 (Embedding)      (None, 200, 128)          2560000   
_________________________________________________________________
bidirectional_1 (Bidirection (None, 200, 128)          99328     
_________________________________________________________________
global_max_pooling1d_1 (Glob (None, 128)               0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 128)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 64)                8256      
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 65        
Total params: 2,667,649
Tr